In [0]:

## Libraries Prequisities
!pip install scikit-learn
!pip install numpy==1.16.1

     |████████████████████████████████| 17.3MB 202kB/s 
ERROR: datascience 0.10.6 has requirement folium==0.2.1, but you'll have folium 0.8.3 which is incompatible.
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
  Found existing installation: numpy 1.18.2
    Uninstalling numpy-1.18.2:
      Successfully uninstalled numpy-1.18.2


In [0]:
https://ieeexplore.ieee.org/document/9043535?denied=
LSTM-CNN Architecture for Human Activity Recognition


In [0]:
import numpy as np
import random
from sklearn.ensemble import RandomForestClassifier, VotingClassifier
from sklearn.metrics.classification import accuracy_score, recall_score, f1_score
import scipy.stats as st

/usr/local/lib/python3.6/dist-packages/sklearn/utils/deprecation.py:144: FutureWarning: The sklearn.metrics.classification module is  deprecated in version 0.22 and will be removed in version 0.24. The corresponding classes / functions should instead be imported from sklearn.metrics. Anything that cannot be imported from sklearn.metrics is now part of the private API.
  warnings.warn(message, FutureWarning)


In [0]:
%tensorflow_version 2.x
import tensorflow as tf
print(tf.__version__)
print(tf.test.gpu_device_name())
print("Num GPUs Available: ", len(tf.config.experimental.list_physical_devices('GPU')))

2.2.0-rc2
/device:GPU:0
Num GPUs Available:  1


In [0]:
from tensorflow.keras.callbacks import Callback

In [0]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
np.random.seed(12227)

In [0]:
def DataPreparation(data_input_file):
  print('JIANGUANG HUANG et al. 2019 {}'.format(data_input_file))
  data = np.load(data_input_file)
  X = data['X']
  X = X[:, 0, :, :]
  Y = data['y']
  folds = data['folds']
  # classes_number = Y.shape[1]
  # Y = np.argmax(Y, axis=1)
  return X,Y,folds

In [0]:
def ReportAccuracies(avg_acc, avg_recall,avg_f1):
  ic_acc = st.t.interval(0.9, len(avg_acc) - 1, loc=np.mean(avg_acc), scale=st.sem(avg_acc))
  ic_recall = st.t.interval(0.9, len(avg_recall) - 1, loc=np.mean(avg_recall), scale=st.sem(avg_recall))
  ic_f1 = st.t.interval(0.9, len(avg_f1) - 1, loc=np.mean(avg_f1), scale=st.sem(avg_f1))
  print('Mean Accuracy[{:.4f}] IC [{:.4f}, {:.4f}]'.format(np.mean(avg_acc), ic_acc[0], ic_acc[1]))
  print('Mean Recall[{:.4f}] IC [{:.4f}, {:.4f}]'.format(np.mean(avg_recall), ic_recall[0], ic_recall[1]))
  print('Mean F1[{:.4f}] IC [{:.4f}, {:.4f}]'.format(np.mean(avg_f1), ic_f1[0], ic_f1[1]))

In [0]:
def Run_JIANGUANG_HUANG(data_input_file):
  X,Y,folds,= DataPreparation(data_input_file)
  # idx = [3, 5, 8, 11, 14, 17, 20] #For MHEALTH
  # idx = [1, 4, 7, 10, 13, 14, 17, 20, 23, 26, 27, 30, 33, 36]#For PAMAP2P
  # idx = [val for val in idx for _ in (0, 1)] #Vertical Kernel-1
  # X = zero_padding_MHEALTH(X)
  avg_acc, avg_recall,avg_f1= Train(X,Y,folds)
  ReportAccuracies(avg_acc, avg_recall,avg_f1 )

In [0]:
def build_model(row,col,num_classes):

  
 
  layers = [
      #  tf.keras.layers.Conv2D(filters=1,kernel_size=(5, 1),strides=1, input_shape=(1,row,col)),
      #  tf.keras.layers.Conv2D(filters=1,kernel_size=(5, 1), strides=1),
      #   tf.keras.layers.Conv2D(filters=1,kernel_size=(5, 1), strides=1),
      #  tf.keras.layers.Conv2D(filters=1,kernel_size=(5, 1), strides=1),
       tf.keras.layers.TimeDistributed(tf.keras.layers.Flatten()),
      #  tf.keras.layers.Reshape((col,row)),
     
        
        tf.keras.layers.LSTM(64,return_sequences=True,  input_shape=(row, col)),
        tf.keras.layers.LSTM(64,return_sequences=True), 
        tf.keras.layers.Conv1D(filters=64,kernel_size=5,strides=2),
        tf.keras.layers.MaxPool1D(pool_size=2,strides = 2),
        tf.keras.layers.Conv1D(filters=128,kernel_size= 3,strides=1),
        tf.keras.layers.GlobalAveragePooling1D(),        
        tf.keras.layers.BatchNormalization(),  
                       

       
        
       
        tf.keras.layers.Dense(num_classes, activation = 'softmax')
    ]
    
  model = tf.keras.Sequential(layers)
  return model

In [0]:
def Train(X,y,folds):
  avg_acc = []
  avg_recall = []
  avg_f1 = []
  n_class = y.shape[1]  
  _,img_rows, img_cols = X.shape
  X=X.reshape(X.shape[0],img_rows,img_cols,1)
  _,_,img_rows, img_cols = X.shape
  print(X.shape)
  for i in range(0, len(folds)):
    train_idx = folds[i][0]
    test_idx = folds[i][1]
    X_train = X[train_idx]
    X_test = X[test_idx]
    model=build_model(img_rows,img_cols,n_class)
    print(model.summary)
    model.compile(loss='categorical_crossentropy', metrics=['accuracy'], optimizer='ADAM')
    model.fit(X_train, y[train_idx], batch_size=192, epochs=200,verbose=1)
    y_pred = model.predict(X_test)
    y_pred = np.argmax(y_pred, axis=1)
    y_true = np.argmax(y[test_idx], axis=1)
    acc_fold = accuracy_score(y_true, y_pred)
    avg_acc.append(acc_fold)
    recall_fold = recall_score(y_true, y_pred, average='macro')
    avg_recall.append(recall_fold)
    f1_fold = f1_score(y_true, y_pred, average='macro')
    avg_f1.append(f1_fold)
    print('Accuracy[{:.4f}] Recall[{:.4f}] F1[{:.4f}] at fold[{}]'.format(acc_fold, recall_fold, f1_fold ,i+1))
    print('________________________________________________________________')
    
  return avg_acc, avg_recall,avg_f1

In [0]:
tf.keras.backend.set_image_data_format('channels_first')

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOSO/MHEALTH.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOSO/MHEALTH.npz
(2555, 250, 23, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f169010bb00>>
Epoch 1/200
12/12 [==============================] - 1s 42ms/step - loss: 0.8964 - accuracy: 0.7178
Epoch 2/200
12/12 [==============================] - 0s 32ms/step - loss: 0.1855 - accuracy: 0.9570
Epoch 3/200
12/12 [==============================] - 0s 32ms/step - loss: 0.0648 - accuracy: 0.9857
Epoch 4/200
12/12 [==============================] - 0s 31ms/step - loss: 0.0389 - accuracy: 0.9891
Epoch 5/200
12/12 [==============================] - 0s 31ms/step - loss: 0.0209 - accuracy: 0.9948
Epoch 6/200
12/12 [==============================] - 0s 32ms/step - loss: 0.0110 - accuracy: 0.9978
Epoch 7/200
12/12 [==============================] - 0s 31ms/step - loss: 0.0069 - accuracy: 1.0000
Epoch 8/200
12/12 [==============================] - 0s 32ms/step - l

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOSO/USCHAD.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOSO/USCHAD.npz
(9824, 500, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7fe8983dc860>>
Epoch 1/200
47/47 [==============================] - 3s 66ms/step - loss: 0.6863 - accuracy: 0.7628
Epoch 2/200
47/47 [==============================] - 3s 60ms/step - loss: 0.2946 - accuracy: 0.8851
Epoch 3/200
47/47 [==============================] - 3s 61ms/step - loss: 0.2259 - accuracy: 0.9053
Epoch 4/200
47/47 [==============================] - 3s 60ms/step - loss: 0.1970 - accuracy: 0.9147
Epoch 5/200
47/47 [==============================] - 3s 60ms/step - loss: 0.1775 - accuracy: 0.9196
Epoch 6/200
47/47 [==============================] - 3s 61ms/step - loss: 0.1649 - accuracy: 0.9217
Epoch 7/200
47/47 [==============================] - 3s 62ms/step - loss: 0.1507 - accuracy: 0.9288
Epoch 8/200
47/47 [==============================] - 3s 59ms/step - los

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD1_1s.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD1_1s.npz
(3771, 50, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7fe8981225f8>>
Epoch 1/200
18/18 [==============================] - 0s 12ms/step - loss: 2.6806 - accuracy: 0.1856
Epoch 2/200
18/18 [==============================] - 0s 11ms/step - loss: 2.2117 - accuracy: 0.3343
Epoch 3/200
18/18 [==============================] - 0s 11ms/step - loss: 1.9542 - accuracy: 0.3993
Epoch 4/200
18/18 [==============================] - 0s 11ms/step - loss: 1.8024 - accuracy: 0.4517
Epoch 5/200
18/18 [==============================] - 0s 11ms/step - loss: 1.6448 - accuracy: 0.4895
Epoch 6/200
18/18 [==============================] - 0s 11ms/step - loss: 1.5256 - accuracy: 0.5261
Epoch 7/200
18/18 [==============================] - 0s 11ms/step - loss: 1.4303 - accuracy: 0.5489
Epoch 8/200
18/18 [==============================] - 0s 10ms/step 

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD2_1s.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD2_1s.npz
(1137, 50, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7fe8902ae860>>
Epoch 1/200
6/6 [==============================] - 0s 12ms/step - loss: 1.4402 - accuracy: 0.4397
Epoch 2/200
6/6 [==============================] - 0s 10ms/step - loss: 0.9098 - accuracy: 0.6302
Epoch 3/200
6/6 [==============================] - 0s 9ms/step - loss: 0.7753 - accuracy: 0.6991
Epoch 4/200
6/6 [==============================] - 0s 10ms/step - loss: 0.6535 - accuracy: 0.7396
Epoch 5/200
6/6 [==============================] - 0s 11ms/step - loss: 0.5442 - accuracy: 0.7903
Epoch 6/200
6/6 [==============================] - 0s 10ms/step - loss: 0.4882 - accuracy: 0.8075
Epoch 7/200
6/6 [==============================] - 0s 9ms/step - loss: 0.4654 - accuracy: 0.7964
Epoch 8/200
6/6 [==============================] - 0s 11ms/step - loss: 0.4066 - a

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOSO/WHARF.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOSO/WHARF.npz
(3871, 160, 3, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7fe3d15a7f60>>
Epoch 1/200
12/12 [==============================] - 0s 24ms/step - loss: 1.6871 - accuracy: 0.4660
Epoch 2/200
12/12 [==============================] - 0s 20ms/step - loss: 1.2317 - accuracy: 0.6204
Epoch 3/200
12/12 [==============================] - 0s 18ms/step - loss: 1.1248 - accuracy: 0.6414
Epoch 4/200
12/12 [==============================] - 0s 18ms/step - loss: 1.0548 - accuracy: 0.6679
Epoch 5/200
12/12 [==============================] - 0s 19ms/step - loss: 0.9881 - accuracy: 0.6738
Epoch 6/200
12/12 [==============================] - 0s 19ms/step - loss: 1.0051 - accuracy: 0.6711
Epoch 7/200
12/12 [==============================] - 0s 19ms/step - loss: 0.9409 - accuracy: 0.6871
Epoch 8/200
12/12 [==============================] - 0s 19ms/step - loss

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Streaming output truncated to the last 5000 lines.
Epoch 122/200
20/20 [==============================] - 0s 19ms/step - loss: 0.1474 - accuracy: 0.9466
Epoch 123/200
20/20 [==============================] - 0s 19ms/step - loss: 0.1367 - accuracy: 0.9517
Epoch 124/200
20/20 [==============================] - 0s 19ms/step - loss: 0.1293 - accuracy: 0.9549
Epoch 125/200
20/20 [==============================] - 0s 19ms/step - loss: 0.1230 - accuracy: 0.9581
Epoch 126/200
20/20 [==============================] - 0s 19ms/step - loss: 0.1115 - accuracy: 0.9616
Epoch 127/200
20/20 [==============================] - 0s 19ms/step - loss: 0.1176 - accuracy: 0.9602
Epoch 128/200
20/20 [==============================] - 0s 19ms/step - loss: 0.1197 - accuracy: 0.9594
Epoch 129/200
20/20 [==============================] - 0s 19ms/step - loss: 0.1115 - accuracy: 0.9621
Epoch 130/200
20/20 [==============================] - 0s 20ms/step - loss: 0.1142 - accuracy: 0.9626
Epoch 131/200
20/20 [==========

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOSO/WISDM.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOSO/WISDM.npz
(20846, 100, 3, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7feec87e1588>>
Epoch 1/200
106/106 [==============================] - 2s 15ms/step - loss: 0.5992 - accuracy: 0.8001
Epoch 2/200
106/106 [==============================] - 1s 13ms/step - loss: 0.3335 - accuracy: 0.8867
Epoch 3/200
106/106 [==============================] - 1s 13ms/step - loss: 0.2834 - accuracy: 0.9029
Epoch 4/200
106/106 [==============================] - 1s 13ms/step - loss: 0.1808 - accuracy: 0.9337
Epoch 5/200
106/106 [==============================] - 1s 13ms/step - loss: 0.1397 - accuracy: 0.9532
Epoch 6/200
106/106 [==============================] - 1s 13ms/step - loss: 0.1365 - accuracy: 0.9529
Epoch 7/200
106/106 [==============================] - 1s 14ms/step - loss: 0.0956 - accuracy: 0.9671
Epoch 8/200
106/106 [==============================] - 1s

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Accuracy[0.4593] Recall[0.2945] F1[0.2954] at fold[2]
________________________________________________________________
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7feec8607e10>>
Epoch 1/200
106/106 [==============================] - 2s 15ms/step - loss: 0.5703 - accuracy: 0.8080
Epoch 2/200
106/106 [==============================] - 1s 13ms/step - loss: 0.2866 - accuracy: 0.8980
Epoch 3/200
106/106 [==============================] - 1s 13ms/step - loss: 0.1911 - accuracy: 0.9311
Epoch 4/200
106/106 [==============================] - 1s 14ms/step - loss: 0.1374 - accuracy: 0.9528
Epoch 5/200
106/106 [==============================] - 1s 13ms/step - loss: 0.1224 - accuracy: 0.9573
Epoch 6/200
106/106 [==============================] - 1s 13ms/step - loss: 0.0917 - accuracy: 0.9674
Epoch 7/200
106/106 [==============================] - 1s 13ms/step - loss: 0.0816 - accuracy: 0.9727
Epoch 8/200
106/106 [==============================] 

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/FNOW/MHEALTH.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/FNOW/MHEALTH.npz
(1335, 250, 23, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7feead51f978>>
Epoch 1/200
7/7 [==============================] - 0s 36ms/step - loss: 1.1792 - accuracy: 0.6600
Epoch 2/200
7/7 [==============================] - 0s 25ms/step - loss: 0.2616 - accuracy: 0.9383
Epoch 3/200
7/7 [==============================] - 0s 23ms/step - loss: 0.1158 - accuracy: 0.9683
Epoch 4/200
7/7 [==============================] - 0s 22ms/step - loss: 0.0680 - accuracy: 0.9842
Epoch 5/200
7/7 [==============================] - 0s 23ms/step - loss: 0.0435 - accuracy: 0.9883
Epoch 6/200
7/7 [==============================] - 0s 23ms/step - loss: 0.0274 - accuracy: 0.9908
Epoch 7/200
7/7 [==============================] - 0s 25ms/step - loss: 0.0280 - accuracy: 0.9917
Epoch 8/200
7/7 [==============================] - 0s 23ms/step - loss: 0.0130 - ac

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/FNOW/USCHAD.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/FNOW/USCHAD.npz
(5038, 500, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7feeac178d68>>
Epoch 1/200
24/24 [==============================] - 2s 70ms/step - loss: 0.9068 - accuracy: 0.6865
Epoch 2/200
24/24 [==============================] - 1s 49ms/step - loss: 0.4084 - accuracy: 0.8417
Epoch 3/200
24/24 [==============================] - 1s 49ms/step - loss: 0.3133 - accuracy: 0.8702
Epoch 4/200
24/24 [==============================] - 1s 49ms/step - loss: 0.2800 - accuracy: 0.8896
Epoch 5/200
24/24 [==============================] - 1s 49ms/step - loss: 0.2392 - accuracy: 0.8998
Epoch 6/200
24/24 [==============================] - 1s 50ms/step - loss: 0.2119 - accuracy: 0.9044
Epoch 7/200
24/24 [==============================] - 1s 50ms/step - loss: 0.1985 - accuracy: 0.9170
Epoch 8/200
24/24 [==============================] - 1s 49ms/step - los

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/FNOW/UTD-MHAD1_1s.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/FNOW/UTD-MHAD1_1s.npz
(2048, 50, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7feec858dd68>>
Epoch 1/200
10/10 [==============================] - 0s 18ms/step - loss: 2.9905 - accuracy: 0.1264
Epoch 2/200
10/10 [==============================] - 0s 9ms/step - loss: 2.3340 - accuracy: 0.2812
Epoch 3/200
10/10 [==============================] - 0s 9ms/step - loss: 2.1043 - accuracy: 0.3597
Epoch 4/200
10/10 [==============================] - 0s 8ms/step - loss: 1.8870 - accuracy: 0.4332
Epoch 5/200
10/10 [==============================] - 0s 9ms/step - loss: 1.7169 - accuracy: 0.4703
Epoch 6/200
10/10 [==============================] - 0s 9ms/step - loss: 1.5794 - accuracy: 0.5128
Epoch 7/200
10/10 [==============================] - 0s 8ms/step - loss: 1.4511 - accuracy: 0.5510
Epoch 8/200
10/10 [==============================] - 0s 8ms/step - loss:

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/FNOW/UTD-MHAD2_1s.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/FNOW/UTD-MHAD2_1s.npz
(616, 50, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7feec8259e10>>
Epoch 1/200
3/3 [==============================] - 0s 34ms/step - loss: 1.8682 - accuracy: 0.2857
Epoch 2/200
3/3 [==============================] - 0s 9ms/step - loss: 1.2152 - accuracy: 0.4973
Epoch 3/200
3/3 [==============================] - 0s 9ms/step - loss: 0.9373 - accuracy: 0.6510
Epoch 4/200
3/3 [==============================] - 0s 9ms/step - loss: 0.8339 - accuracy: 0.6962
Epoch 5/200
3/3 [==============================] - 0s 9ms/step - loss: 0.7678 - accuracy: 0.7179
Epoch 6/200
3/3 [==============================] - 0s 8ms/step - loss: 0.6634 - accuracy: 0.7450
Epoch 7/200
3/3 [==============================] - 0s 8ms/step - loss: 0.5868 - accuracy: 0.7776
Epoch 8/200
3/3 [==============================] - 0s 8ms/step - loss: 0.5055 - accurac

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/FNOW/WHARF.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/FNOW/WHARF.npz
(2146, 160, 3, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7feec025b400>>
Epoch 1/200
11/11 [==============================] - 0s 23ms/step - loss: 1.8457 - accuracy: 0.4123
Epoch 2/200
11/11 [==============================] - 0s 17ms/step - loss: 1.4396 - accuracy: 0.5156
Epoch 3/200
11/11 [==============================] - 0s 17ms/step - loss: 1.3324 - accuracy: 0.5852
Epoch 4/200
11/11 [==============================] - 0s 16ms/step - loss: 1.1668 - accuracy: 0.6163
Epoch 5/200
11/11 [==============================] - 0s 16ms/step - loss: 1.0598 - accuracy: 0.6412
Epoch 6/200
11/11 [==============================] - 0s 17ms/step - loss: 1.0452 - accuracy: 0.6687
Epoch 7/200
11/11 [==============================] - 0s 17ms/step - loss: 0.9982 - accuracy: 0.6796
Epoch 8/200
11/11 [==============================] - 0s 16ms/step - loss

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/FNOW/WISDM.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/FNOW/WISDM.npz
(10516, 100, 3, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7feead4d2e80>>
Epoch 1/200
50/50 [==============================] - 1s 16ms/step - loss: 0.7191 - accuracy: 0.7565
Epoch 2/200
50/50 [==============================] - 1s 14ms/step - loss: 0.4543 - accuracy: 0.8400
Epoch 3/200
50/50 [==============================] - 1s 13ms/step - loss: 0.3643 - accuracy: 0.8676
Epoch 4/200
50/50 [==============================] - 1s 13ms/step - loss: 0.2749 - accuracy: 0.9018
Epoch 5/200
50/50 [==============================] - 1s 14ms/step - loss: 0.2346 - accuracy: 0.9176
Epoch 6/200
50/50 [==============================] - 1s 13ms/step - loss: 0.1811 - accuracy: 0.9332
Epoch 7/200
50/50 [==============================] - 1s 13ms/step - loss: 0.1748 - accuracy: 0.9402
Epoch 8/200
50/50 [==============================] - 1s 14ms/step - los

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOTO/MHEALTH.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOTO/MHEALTH.npz
(2555, 250, 23, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7feea445fda0>>
Epoch 1/200
12/12 [==============================] - 1s 51ms/step - loss: 0.8885 - accuracy: 0.7612
Epoch 2/200
12/12 [==============================] - 0s 28ms/step - loss: 0.1294 - accuracy: 0.9696
Epoch 3/200
12/12 [==============================] - 0s 27ms/step - loss: 0.0598 - accuracy: 0.9822
Epoch 4/200
12/12 [==============================] - 0s 27ms/step - loss: 0.0309 - accuracy: 0.9913
Epoch 5/200
12/12 [==============================] - 0s 27ms/step - loss: 0.0166 - accuracy: 0.9974
Epoch 6/200
12/12 [==============================] - 0s 27ms/step - loss: 0.0088 - accuracy: 0.9996
Epoch 7/200
12/12 [==============================] - 0s 27ms/step - loss: 0.0052 - accuracy: 1.0000
Epoch 8/200
12/12 [==============================] - 0s 27ms/step - l

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOTO/USCHAD.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOTO/USCHAD.npz
(9824, 500, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7feec06f6048>>
Epoch 1/200
46/46 [==============================] - 3s 69ms/step - loss: 0.6490 - accuracy: 0.7762
Epoch 2/200
46/46 [==============================] - 2s 51ms/step - loss: 0.2801 - accuracy: 0.8890
Epoch 3/200
46/46 [==============================] - 2s 51ms/step - loss: 0.2186 - accuracy: 0.9092
Epoch 4/200
46/46 [==============================] - 2s 52ms/step - loss: 0.1861 - accuracy: 0.9163
Epoch 5/200
46/46 [==============================] - 2s 52ms/step - loss: 0.1684 - accuracy: 0.9251
Epoch 6/200
46/46 [==============================] - 2s 52ms/step - loss: 0.1577 - accuracy: 0.9255
Epoch 7/200
46/46 [==============================] - 2s 52ms/step - loss: 0.1509 - accuracy: 0.9260
Epoch 8/200
46/46 [==============================] - 2s 52ms/step - los

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD1_1s.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD1_1s.npz
(3771, 50, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f3d21c4b780>>
Epoch 1/200
18/18 [==============================] - 0s 11ms/step - loss: 2.7144 - accuracy: 0.1950
Epoch 2/200
18/18 [==============================] - 0s 9ms/step - loss: 2.2074 - accuracy: 0.3213
Epoch 3/200
18/18 [==============================] - 0s 9ms/step - loss: 1.9473 - accuracy: 0.4030
Epoch 4/200
18/18 [==============================] - 0s 9ms/step - loss: 1.7505 - accuracy: 0.4568
Epoch 5/200
18/18 [==============================] - 0s 10ms/step - loss: 1.5898 - accuracy: 0.4991
Epoch 6/200
18/18 [==============================] - 0s 9ms/step - loss: 1.4947 - accuracy: 0.5311
Epoch 7/200
18/18 [==============================] - 0s 9ms/step - loss: 1.3620 - accuracy: 0.5786
Epoch 8/200
18/18 [==============================] - 0s 9ms/step - loss

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD2_1s.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD2_1s.npz
(1137, 50, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f3d2015af28>>
Epoch 1/200
6/6 [==============================] - 0s 11ms/step - loss: 1.5718 - accuracy: 0.4098
Epoch 2/200
6/6 [==============================] - 0s 8ms/step - loss: 1.0373 - accuracy: 0.6188
Epoch 3/200
6/6 [==============================] - 0s 9ms/step - loss: 0.7486 - accuracy: 0.6881
Epoch 4/200
6/6 [==============================] - 0s 8ms/step - loss: 0.6761 - accuracy: 0.6993
Epoch 5/200
6/6 [==============================] - 0s 8ms/step - loss: 0.6070 - accuracy: 0.7686
Epoch 6/200
6/6 [==============================] - 0s 7ms/step - loss: 0.4817 - accuracy: 0.8206
Epoch 7/200
6/6 [==============================] - 0s 7ms/step - loss: 0.4585 - accuracy: 0.8135
Epoch 8/200
6/6 [==============================] - 0s 7ms/step - loss: 0.4583 - accura

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOTO/WHARF.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOTO/WHARF.npz
(3871, 160, 3, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f3cd1ba8dd8>>
Epoch 1/200
19/19 [==============================] - 0s 21ms/step - loss: 1.4461 - accuracy: 0.5377
Epoch 2/200
19/19 [==============================] - 0s 19ms/step - loss: 1.1082 - accuracy: 0.6380
Epoch 3/200
19/19 [==============================] - 0s 19ms/step - loss: 1.0019 - accuracy: 0.6607
Epoch 4/200
19/19 [==============================] - 0s 19ms/step - loss: 0.9218 - accuracy: 0.6918
Epoch 5/200
19/19 [==============================] - 0s 19ms/step - loss: 0.8383 - accuracy: 0.7154
Epoch 6/200
19/19 [==============================] - 0s 19ms/step - loss: 0.8014 - accuracy: 0.7128
Epoch 7/200
19/19 [==============================] - 0s 19ms/step - loss: 0.7776 - accuracy: 0.7296
Epoch 8/200
19/19 [==============================] - 0s 19ms/step - loss

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/LOTO/WISDM.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/LOTO/WISDM.npz
(20846, 100, 3, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f9b265245c0>>
Epoch 1/200
96/96 [==============================] - 2s 19ms/step - loss: 0.6315 - accuracy: 0.7873
Epoch 2/200
96/96 [==============================] - 2s 18ms/step - loss: 0.3316 - accuracy: 0.8801
Epoch 3/200
96/96 [==============================] - 2s 18ms/step - loss: 0.2314 - accuracy: 0.9165
Epoch 4/200
96/96 [==============================] - 2s 18ms/step - loss: 0.1567 - accuracy: 0.9454
Epoch 5/200
96/96 [==============================] - 2s 19ms/step - loss: 0.1289 - accuracy: 0.9566
Epoch 6/200
96/96 [==============================] - 2s 18ms/step - loss: 0.1069 - accuracy: 0.9639
Epoch 7/200
96/96 [==============================] - 2s 18ms/step - loss: 0.0857 - accuracy: 0.9698
Epoch 8/200
96/96 [==============================] - 2s 19ms/step - los

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/SNOW/MHEALTH.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/SNOW/MHEALTH.npz
(2555, 250, 23, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f3cd24eba20>>
Epoch 1/200
12/12 [==============================] - 0s 37ms/step - loss: 0.8051 - accuracy: 0.7488
Epoch 2/200
12/12 [==============================] - 0s 30ms/step - loss: 0.1369 - accuracy: 0.9604
Epoch 3/200
12/12 [==============================] - 0s 30ms/step - loss: 0.0470 - accuracy: 0.9917
Epoch 4/200
12/12 [==============================] - 0s 30ms/step - loss: 0.0233 - accuracy: 0.9961
Epoch 5/200
12/12 [==============================] - 0s 30ms/step - loss: 0.0119 - accuracy: 0.9987
Epoch 6/200
12/12 [==============================] - 0s 30ms/step - loss: 0.0073 - accuracy: 0.9996
Epoch 7/200
12/12 [==============================] - 0s 30ms/step - loss: 0.0045 - accuracy: 0.9996
Epoch 8/200
12/12 [==============================] - 0s 30ms/step - l

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/SNOW/USCHAD.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/SNOW/USCHAD.npz
(9824, 500, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f9aff52dda0>>
Epoch 1/200
47/47 [==============================] - 4s 81ms/step - loss: 0.7155 - accuracy: 0.7500
Epoch 2/200
47/47 [==============================] - 4s 79ms/step - loss: 0.3350 - accuracy: 0.8671
Epoch 3/200
47/47 [==============================] - 4s 79ms/step - loss: 0.2576 - accuracy: 0.8970
Epoch 4/200
47/47 [==============================] - 4s 79ms/step - loss: 0.3076 - accuracy: 0.8925
Epoch 5/200
47/47 [==============================] - 4s 80ms/step - loss: 0.2589 - accuracy: 0.8977
Epoch 6/200
47/47 [==============================] - 4s 79ms/step - loss: 0.2278 - accuracy: 0.9036
Epoch 7/200
47/47 [==============================] - 4s 79ms/step - loss: 0.2150 - accuracy: 0.9060
Epoch 8/200
47/47 [==============================] - 4s 79ms/step - los

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/SNOW/UTD-MHAD1_1s.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/SNOW/UTD-MHAD1_1s.npz
(3771, 50, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f3cd35d59b0>>
Epoch 1/200
18/18 [==============================] - 0s 10ms/step - loss: 2.7399 - accuracy: 0.1807
Epoch 2/200
18/18 [==============================] - 0s 9ms/step - loss: 2.1800 - accuracy: 0.3308
Epoch 3/200
18/18 [==============================] - 0s 9ms/step - loss: 1.9306 - accuracy: 0.4025
Epoch 4/200
18/18 [==============================] - 0s 9ms/step - loss: 1.7533 - accuracy: 0.4551
Epoch 5/200
18/18 [==============================] - 0s 9ms/step - loss: 1.5743 - accuracy: 0.5100
Epoch 6/200
18/18 [==============================] - 0s 9ms/step - loss: 1.4616 - accuracy: 0.5434
Epoch 7/200
18/18 [==============================] - 0s 9ms/step - loss: 1.3393 - accuracy: 0.5791
Epoch 8/200
18/18 [==============================] - 0s 9ms/step - loss:

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/SNOW/UTD-MHAD2_1s.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/SNOW/UTD-MHAD2_1s.npz
(1137, 50, 6, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f3cd2f949b0>>
Epoch 1/200
6/6 [==============================] - 0s 12ms/step - loss: 1.4127 - accuracy: 0.4465
Epoch 2/200
6/6 [==============================] - 0s 8ms/step - loss: 0.9033 - accuracy: 0.6271
Epoch 3/200
6/6 [==============================] - 0s 7ms/step - loss: 0.7591 - accuracy: 0.7085
Epoch 4/200
6/6 [==============================] - 0s 8ms/step - loss: 0.6622 - accuracy: 0.7468
Epoch 5/200
6/6 [==============================] - 0s 8ms/step - loss: 0.5486 - accuracy: 0.7929
Epoch 6/200
6/6 [==============================] - 0s 8ms/step - loss: 0.4622 - accuracy: 0.8194
Epoch 7/200
6/6 [==============================] - 0s 8ms/step - loss: 0.4112 - accuracy: 0.8489
Epoch 8/200
6/6 [==============================] - 0s 8ms/step - loss: 0.3755 - accura

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/SNOW/WHARF.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/SNOW/WHARF.npz
(3880, 160, 3, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f3cd0609828>>
Epoch 1/200
19/19 [==============================] - 0s 22ms/step - loss: 1.4748 - accuracy: 0.5337
Epoch 2/200
19/19 [==============================] - 0s 19ms/step - loss: 1.1586 - accuracy: 0.6298
Epoch 3/200
19/19 [==============================] - 0s 19ms/step - loss: 1.0322 - accuracy: 0.6643
Epoch 4/200
19/19 [==============================] - 0s 19ms/step - loss: 0.9132 - accuracy: 0.6984
Epoch 5/200
19/19 [==============================] - 0s 19ms/step - loss: 0.8485 - accuracy: 0.7220
Epoch 6/200
19/19 [==============================] - 0s 19ms/step - loss: 0.7966 - accuracy: 0.7291
Epoch 7/200
19/19 [==============================] - 0s 19ms/step - loss: 0.7812 - accuracy: 0.7286
Epoch 8/200
19/19 [==============================] - 0s 19ms/step - loss

In [0]:
Run_JIANGUANG_HUANG('/content/drive/My Drive/Computer_vision_project/data/SNOW/WISDM.npz')

JIANGUANG HUANG et al. 2019 /content/drive/My Drive/Computer_vision_project/data/SNOW/WISDM.npz
(20846, 100, 3, 1)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f9b26243e48>>
Epoch 1/200
98/98 [==============================] - 2s 19ms/step - loss: 0.6113 - accuracy: 0.7918
Epoch 2/200
98/98 [==============================] - 2s 19ms/step - loss: 0.3200 - accuracy: 0.8875
Epoch 3/200
98/98 [==============================] - 2s 19ms/step - loss: 0.2218 - accuracy: 0.9200
Epoch 4/200
98/98 [==============================] - 2s 18ms/step - loss: 0.1555 - accuracy: 0.9430
Epoch 5/200
98/98 [==============================] - 2s 18ms/step - loss: 0.1291 - accuracy: 0.9540
Epoch 6/200
98/98 [==============================] - 2s 19ms/step - loss: 0.1088 - accuracy: 0.9620
Epoch 7/200
98/98 [==============================] - 2s 19ms/step - loss: 0.0956 - accuracy: 0.9683
Epoch 8/200
98/98 [==============================] - 2s 18ms/step - los